In [2]:
import pandas as pd
import altair as alt
# Lemmatization 

import nltk
import string
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer

import gensim 
from gensim.models import LdaModel
from gensim.models.wrappers import LdaMallet

import gensim.corpora as corpora
from gensim.corpora import Dictionary
from gensim import matutils, models


In [6]:
# Reading data from 1997 to 2012
# Only The City of Vancouver will be considered
old_data = pd.read_csv("Data/business-licences-1997-to-2012.csv", sep = ";")
old_data = old_data.query("City == 'Vancouver'")

# Reading new data from 2013 to 2020
new_data = pd.read_csv("Data/business-licences.csv", sep = ";")
new_data = new_data.query("City == 'Vancouver'")

/Users/eitharelbasheer/opt/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3063: DtypeWarning: Columns (13) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


> will update FOLDERYEAR to be in the correct format before moving on

In [7]:
# Training set contains data from 1997 up until 2015
data = pd.concat([old_data, new_data])
data.FOLDERYEAR = data.FOLDERYEAR.apply(lambda x: 1900 + x if x > 90 else 2000 + x)

In [9]:
data.to_csv("Data/data.csv")

## EDA

In [10]:
train.shape[0] - train.LicenceRSN.nunique()

475

> Some duplicate RSNs. (Noted in the documentaion)

In [11]:
train.groupby(by = "FOLDERYEAR").LicenceNumber.nunique()

FOLDERYEAR
1996.0        6
1997.0    43673
1998.0    49072
1999.0    49899
2000.0    50429
2001.0    52594
2002.0    51544
2003.0    52478
2004.0    52842
2005.0    53525
2006.0    52487
2007.0    51190
2008.0    51383
2009.0    52220
2010.0    52616
2011.0    52369
2012.0    52217
2013.0    51250
2014.0    50932
2015.0    51379
2016.0    52158
2017.0    51951
Name: LicenceNumber, dtype: int64

> I believe that year 96 is not useful and can be dropped. 

In [12]:
data = data.query("FOLDERYEAR != 1996.0")

In [13]:
data.isna().any()

FOLDERYEAR                True
LicenceRSN               False
LicenceNumber            False
LicenceRevisionNumber     True
BusinessName              True
BusinessTradeName         True
Status                   False
IssuedDate                True
ExpiredDate               True
BusinessType             False
BusinessSubType           True
Unit                      True
UnitType                  True
House                     True
Street                    True
City                     False
Province                  True
Country                   True
PostalCode                True
LocalArea                 True
NumberofEmployees        False
FeePaid                   True
ExtractDate              False
Geom                      True
dtype: bool

> Many missing values. Luckily, non in LicenceRSN.

In [14]:
train.Status.unique()

array(['Issued', 'Pending', 'Gone Out of Business', 'Inactive',
       'Cancelled', 'Invalid Status Code'], dtype=object)

In [17]:
train.Status.value_counts()

Issued                  894103
Gone Out of Business    100419
Pending                  56163
Inactive                 22489
Cancelled                14784
Invalid Status Code          3
Name: Status, dtype: int64

> Will only consider the Issued licences.

In [18]:
train.IssuedDate

0                         2006-01-10
1                         2006-01-10
2                         2006-01-11
3                         2006-01-11
4                         2005-12-08
                     ...            
1087956    2017-05-01T08:55:24-07:00
1087957    2017-05-01T11:14:36-07:00
1087958    2017-05-05T10:48:40-07:00
1087959    2017-06-04T16:47:23-07:00
1087960    2017-05-01T15:51:11-07:00
Name: IssuedDate, Length: 1087961, dtype: object

> Issue date is not consistent.

In [262]:
train.ExpiredDate

0         2006-12-31
1         2006-12-31
2         2006-12-31
3         2006-12-31
4         2006-12-31
             ...    
302810    2015-12-31
302811    2015-12-31
302812           NaN
302813           NaN
302814    2015-12-31
Name: ExpiredDate, Length: 980805, dtype: object

In [20]:
data = data.query("Status == 'Issued'")
data.IssuedDate = data.IssuedDate.str.extract(r'(\d{4}\-\d{2}\-\d{2}).*', expand = False)

### A look at the Business Type Distribution in Downtown Area

In [21]:
Downtown = dataset.query("LocalArea == 'Downtown'")

In [22]:
Downtown = Downtown.groupby(by = ["FOLDERYEAR", "BusinessType"]).count().reset_index()[["FOLDERYEAR", "BusinessType", "LicenceRSN"]]

In [28]:
alt.renderers.enable('mimetype')
alt.Chart(Downtown).mark_line().encode(
    x='FOLDERYEAR:N',
    y="LicenceRSN:Q",
    color = "BusinessType"
).properties(width = 600, height = 400, title = "Business Type Distribution in Vancouver Downtown Area")

alt.Chart(...)

> We got a taste of the change of the number and type of businesses in downtown Vancouver. 

> Seems for most of the Businesses the number was pretty stable. 

## Analysis

> NLP peprocessing to clean the BusinessType cloumn is needed.

In [29]:
punc = list(string.punctuation)
stop_words = list(set(stopwords.words('english')))
punctuation = string.punctuation
stop_words += list(punctuation)
stop_words.extend(['``','’', '`','br','"',"”", "''", "'s"]) 

def nlp(text):
    
    """
    Performs NLP preprocessing including tokenization, stop-words removal and Lemmatiztion.
    
    Parameters
    -----------------
    text: input text (str)
    
    Returns
    ------------------
    a list containing the words of the preprocessed text
    
    """
    for p in punc:
        text = text.replace(p, "")
    preprocessed = []    
    tokenized = word_tokenize(text)
    for token in tokenized:
        token = token.lower()
        if token not in stop_words:
            preprocessed.append(token)
    lemmatizer= WordNetLemmatizer()
    
    lemmatized = []
    for word in preprocessed:
        lemmatized.append(lemmatizer.lemmatize(word,'n'))
    return " ".join(lemmatized) 

In [32]:
# import spacy
# import en_core_web_sm
# nlp = en_core_web_sm.load()
# stop_words = list(set(stopwords.words('english')))
# stop_words += list(punctuation)
# stop_words.extend(['``','’', '`','br','"',"”", "''", "'s"]) 

In [33]:

# def nlp_preprocess(text, irrelevant_pos = ['ADV','PRON','CCONJ','PUNCT','PART','DET','ADP','SPACE']):
    
#     """
#     Performs NLP preprocessing including tokenization, stop-words removal and Lemmatiztion.
    
#     Parameters
#     -----------------
#     text: input text (str)
    
#     Returns
#     ------------------
#     a list containing the words of the preprocessed text
    
#     """
#     doc = nlp(text)
#     output = ""
#     for token in doc:
#         if token.text not in stop_words and token.pos_ not in irrelevant_pos:
#             output = output+" "+token.lemma_
#     return output[1:] 

In [ ]:
from pandarallel import pandarallel

pandarallel.initialize()
data['BusinessType'] = data['BusinessType'].parallel_apply(nlp)

### Building LDA Topic Model for Bussiness Types

In [37]:
corpus = [doc.split() for doc in data['BusinessType'].tolist()]
dictionary = corpora.Dictionary(corpus)
doc_term_matrix = [dictionary.doc2bow(doc) for doc in corpus]

In [38]:
model_lda2 = models.LdaModel(corpus=doc_term_matrix, 
                      id2word=dictionary, 
                      num_topics=15, passes = 3)

model_lda2.print_topics()

[(0,
  '0.361*"repair" + 0.197*"auto" + 0.184*"servicemaintenance" + 0.138*"painter" + 0.040*"body" + 0.040*"shop" + 0.020*"boot" + 0.020*"shoe" + 0.000*"duplex" + 0.000*"community"'),
 (1,
  '0.465*"dealer" + 0.419*"retail" + 0.037*"estate" + 0.037*"real" + 0.020*"entertainment" + 0.015*"secondhand" + 0.007*"grocery" + 0.000*"market" + 0.000*"outlet" + 0.000*"centre"'),
 (2,
  '0.338*"auto" + 0.227*"parking" + 0.225*"lotparkade" + 0.119*"educational" + 0.043*"exhibitionsshowsconcerts" + 0.025*"detailing" + 0.010*"wholesaler" + 0.009*"washer" + 0.002*"backyard" + 0.002*"pay"'),
 (3,
  '0.327*"class" + 0.327*"restaurant" + 0.323*"1" + 0.015*"laboratory" + 0.004*"2" + 0.002*"salon" + 0.002*"tanning" + 0.000*"hairdressing" + 0.000*"karaoke" + 0.000*"duplex"'),
 (4,
  '0.251*"liquor" + 0.185*"store" + 0.172*"movingtransfer" + 0.102*"amendment" + 0.102*"licence" + 0.102*"temp" + 0.023*"pet" + 0.021*"psychicfortune" + 0.021*"teller" + 0.014*"adult"'),
 (5,
  '0.827*"food" + 0.077*"plumber" +

In [42]:
# Save model to disk.
from gensim.test.utils import datapath
temp_file = datapath("model_lda")
model_lda2.save(temp_file)

In [129]:
# lda = LdaModel.load(temp_file)

In [43]:
topic_labels = {0:'Car Services', 1: 'Dealer and Retailer', 2:'Parkade', 3: 'Resutaurant', 4: 'liquor and Adult store', 5: 'Food Retailer' , 6: 'Contractor', 7: 'Rental and Booking Agency', 8: 'Catering and Food Delivery', 9: "Hiring Agency",
               10: "Hotel and Rental Agency", 11: 'Dwelling Office', 12: 'Beauty Salon', 13: 'Rental Management services', 14: 'Contractor and Freelancer'}

In [44]:
vec = doc_term_matrix

topics = model_lda2[vec]
result = list()


In [46]:
topic_match = [topic_labels[max(element,key=lambda item:item[1])[0]] for element in topics]

In [47]:
data["Business_type_pp"] = pd.Series(topic_match)

In [51]:
data.to_csv("Data/data.csv")

In [52]:
data[0:10]

FOLDERYEAR  LicenceRSN LicenceNumber  LicenceRevisionNumber  \
0      2006.0     1012386     06-141888                    0.0   
1      2006.0     1012387     06-141889                    0.0   
2      2006.0     1012388     06-141890                    0.0   
3      2006.0     1012389     06-141891                    0.0   
4      2006.0     1012390     06-141892                    0.0   
5      2006.0     1012392     06-141894                    0.0   
6      2006.0     1012393     06-141895                    0.0   
7      2006.0     1012397     06-141899                    0.0   
8      2006.0     1012398     06-141900                    0.0   
9      2006.0     1012402     06-141904                    0.0   

                                   BusinessName  \
0                 True Confections Broadway Inc   
1                 True Confections Broadway Inc   
2                         Iso's Enterprises Ltd   
3                         Iso's Enterprises Ltd   
4       Tsui Hang Village Restaurant (1988) Ltd   
5                             Tsunami Sushi Ltd   
6                             Tsunami Sushi Ltd   
7                      Triple Gold Holdings Ltd   
8                          Toto Enterprises Ltd   
9  United Croats Of Canada King Tomislav Branch   

                      BusinessTradeName  Status  IssuedDate ExpiredDate  \
0    True Confections Desert Restaurant  Issued  2006-01-10  2006-12-31   
1    True Confections Desert Restaurant  Issued  2006-01-10  2006-12-31   
2                Jade Rabbit Restaurant  Issued  2006-01-11  2006-12-31   
3                Jade Rabbit Restaurant  Issued  2006-01-11  2006-12-31   
4  Tsui Hang Village Seafood Restaurant  Issued  2005-12-08  2006-12-31   
5              Tsunami Sushi Restaurant  Issued  2005-12-09  2006-12-31   
6              Tsunami Sushi Restaurant  Issued  2005-12-09  2006-12-31   
7                Golden Swan Restaurant  Issued  2006-01-17  2006-12-31   
8                               Cin Cin  Issued  2005-12-13  2006-12-31   
9                                   NaN  Issued  2005-12-09  2006-12-31   

                    BusinessType  ...       City Province Country PostalCode  \
0         dining lounge historic  ...  Vancouver       BC      CA    V6R 2B9   
1             restaurant class 1  ...  Vancouver       BC      CA    V6R 2B9   
2         dining lounge historic  ...  Vancouver       BC      CA    V6P 3E9   
3             restaurant class 1  ...  Vancouver       BC      CA    V6P 3E9   
4         dining lounge historic  ...  Vancouver       BC     NaN    V6Z 1M1   
5         dining lounge historic  ...  Vancouver       BC      CA    V6E 4A9   
6             restaurant class 1  ...  Vancouver       BC      CA    V6E 4A9   
7             restaurant class 1  ...  Vancouver       BC      CA    V5P 3V7   
8         dining lounge historic  ...  Vancouver       BC      CA    V6E 1B2   
9  liquor establishment standard  ...  Vancouver       BC      CA    V5N 4E5   

                  LocalArea NumberofEmployees FeePaid  \
0           West Point Grey               0.0   167.0   
1           West Point Grey               0.0   558.0   
2                   Marpole               0.0   330.0   
3                   Marpole               0.0   558.0   
4                  Downtown               0.0   704.0   
5                  West End               0.0   290.0   
6                  West End               0.0   558.0   
7  Kensington-Cedar Cottage               0.0   558.0   
8                  West End               0.0   946.0   
9  Kensington-Cedar Cottage               0.0   342.0   

                 ExtractDate  \
0  2019-07-21T06:48:41-07:00   
1  2019-07-21T06:48:41-07:00   
2  2019-07-21T06:48:41-07:00   
3  2019-07-21T06:48:41-07:00   
4  2019-07-21T06:48:41-07:00   
5  2019-07-21T06:48:41-07:00   
6  2019-07-21T06:48:41-07:00   
7  2019-07-21T06:48:41-07:00   
8  2019-07-21T06:48:41-07:00   
9  2019-07-21T06:48:41-07:00   

                          

### Altair plots

In [42]:
dataset = pd.read_csv("Data/data.csv").dropna(subset=['Geom', 'LocalArea'])[["FOLDERYEAR", "LicenceRSN", "LocalArea", "Business_type_pp", "Geom"]]

/Users/eitharelbasheer/opt/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3063: DtypeWarning: Columns (14) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [25]:
dataset.head()

FOLDERYEAR  LicenceRSN        LocalArea         Business_type_pp  \
0      2006.0     1012386  West Point Grey  Hotel and Rental Agency   
1      2006.0     1012387  West Point Grey              Resutaurant   
2      2006.0     1012388          Marpole  Hotel and Rental Agency   
3      2006.0     1012389          Marpole              Resutaurant   
4      2006.0     1012390         Downtown  Hotel and Rental Agency   

            X          Y  
0 -123.186102  49.264622  
1 -123.186102  49.264622  
2 -123.135012  49.204070  
3 -123.135012  49.204070  
4 -123.126312  49.277468

In [43]:
import ast 

In [44]:
dataset["X"] = dataset.Geom.apply(lambda x: ast.literal_eval(x)['coordinates'][0])
dataset["Y"] = dataset.Geom.apply(lambda x: ast.literal_eval(x)['coordinates'][1])

In [45]:
dataset = dataset.drop(columns = ["Geom"])

In [58]:
dataset.groupby(by = ["LocalArea"])["X"].apply(list).reset_index()

LocalArea  \
0              Arbutus-Ridge   
1                   Downtown   
2          Dunbar-Southlands   
3                   Fairview   
4         Grandview-Woodland   
5           Hastings-Sunrise   
6   Kensington-Cedar Cottage   
7                 Kerrisdale   
8                  Killarney   
9                  Kitsilano   
10                   Marpole   
11            Mount Pleasant   
12                  Oakridge   
13       Renfrew-Collingwood   
14                Riley Park   
15               Shaughnessy   
16              South Cambie   
17                Strathcona   
18                    Sunset   
19       Victoria-Fraserview   
20                  West End   
21           West Point Grey   

                                                    X  
0   [-123.157470632759, -123.156748642132, -123.15...  
1   [-123.126312429854, -123.115620015702, -123.10...  
2   [-123.18546909103, -123.184751183506, -123.184...  
3   [-123.125687280142, -123.122237018287, -123.12...  
4   [-123.066233984148, -123.075261296607, -123.07...  
5   [-123.039016311434, -123.056162054502, -123.04...  
6   [-123.083003454044, -123.058852970252, -123.06...  
7   [-123.157848077891, -123.157848077891, -123.15...  
8   [-123.034953638269, -123.034953638269, -123.03...  
9   [-123.157330516314, -123.146512582061, -123.14...  
10  [-123.135012244527, -123.135012244527, -123.14...  
11  [-123.10067674604, -123.099738690252, -123.108...  
12  [-123.118854822642, -123.125991228508, -123.11...  
13  [-123.03231649783, -123.046053218613, -123.029...  
14  [-123.100874649626, -123.100874649626, -123.10...  
15  [-123.134604029974, -123.128026015946, -123.15...  
16  [-123.121522309399, -123.127087458671, -123.11...  
17  [-123.096463436136, -123.085317045165, -123.08...  
18  [-123.091161903356, -123.102585189866, -123.09...  
19  [-123.065384270628, -123.06516343121, -123.066...  
20  [-123.12335652139, -123.12335652139, -123.1263...  
21  [-123.186102026338, -123.186102026338, -123.20...

In [46]:
# Get longitude and latitude ranges for each erea
X = dataset.groupby(by = ["LocalArea"])["X"].apply(list).reset_index()
Y = dataset.groupby(by = ["LocalArea"])["Y"].apply(list).reset_index()

In [ ]:
dataset.apply(lambda x: X.q)

In [54]:
X

LocalArea  \
0              Arbutus-Ridge   
1                   Downtown   
2          Dunbar-Southlands   
3                   Fairview   
4         Grandview-Woodland   
5           Hastings-Sunrise   
6   Kensington-Cedar Cottage   
7                 Kerrisdale   
8                  Killarney   
9                  Kitsilano   
10                   Marpole   
11            Mount Pleasant   
12                  Oakridge   
13       Renfrew-Collingwood   
14                Riley Park   
15               Shaughnessy   
16              South Cambie   
17                Strathcona   
18                    Sunset   
19       Victoria-Fraserview   
20                  West End   
21           West Point Grey   

                                                    X  
0   [-123.157470632759, -123.156748642132, -123.15...  
1   [-123.126312429854, -123.115620015702, -123.10...  
2   [-123.18546909103, -123.184751183506, -123.184...  
3   [-123.125687280142, -123.122237018287, -123.12...  
4   [-123.066233984148, -123.075261296607, -123.07...  
5   [-123.039016311434, -123.056162054502, -123.04...  
6   [-123.083003454044, -123.058852970252, -123.06...  
7   [-123.157848077891, -123.157848077891, -123.15...  
8   [-123.034953638269, -123.034953638269, -123.03...  
9   [-123.157330516314, -123.146512582061, -123.14...  
10  [-123.135012244527, -123.135012244527, -123.14...  
11  [-123.10067674604, -123.099738690252, -123.108...  
12  [-123.118854822642, -123.125991228508, -123.11...  
13  [-123.03231649783, -123.046053218613, -123.029...  
14  [-123.100874649626, -123.100874649626, -123.10...  
15  [-123.134604029974, -123.128026015946, -123.15...  
16  [-123.121522309399, -123.127087458671, -123.11...  
17  [-123.096463436136, -123.085317045165, -123.08...  
18  [-123.091161903356, -123.102585189866, -123.09...  
19  [-123.065384270628, -123.06516343121, -123.066...  
20  [-123.12335652139, -123.12335652139, -123.1263...  
21  [-123.186102026338, -123.186102026338, -123.20...

In [47]:
dataset.isna().any()

FOLDERYEAR          False
LicenceRSN          False
LocalArea           False
Business_type_pp    False
X                   False
Y                   False
dtype: bool

In [51]:
dataset.dtypes

FOLDERYEAR          float64
LicenceRSN            int64
LocalArea            object
Business_type_pp     object
X                   float64
Y                   float64
dtype: object

In [65]:
pd.concat([X, dataset],join = "inner")

LocalArea                                                  X
0             Arbutus-Ridge  [-123.157470632759, -123.156748642132, -123.15...
1                  Downtown  [-123.126312429854, -123.115620015702, -123.10...
2         Dunbar-Southlands  [-123.18546909103, -123.184751183506, -123.184...
3                  Fairview  [-123.125687280142, -123.122237018287, -123.12...
4        Grandview-Woodland  [-123.066233984148, -123.075261296607, -123.07...
...                     ...                                                ...
1038652          Strathcona                                           -123.095
1038655            West End                                            -123.13
1038657    Hastings-Sunrise                                           -123.037
1038658            Downtown                                           -123.115
1038659            Downtown                                           -123.113

[630190 rows x 2 columns]

In [8]:
import geopandas as gpd

gdataset = geopandas.GeoDataFrame(
    dataset, geometry=geopandas.points_from_xy(dataset.X, dataset.Y))

In [104]:
gdataset.head()

Unnamed: 0  FOLDERYEAR  LicenceRSN LicenceNumber  LicenceRevisionNumber  \
0           0      2006.0     1012386     06-141888                    0.0   
1           1      2006.0     1012387     06-141889                    0.0   
2           2      2006.0     1012388     06-141890                    0.0   
3           3      2006.0     1012389     06-141891                    0.0   
4           4      2006.0     1012390     06-141892                    0.0   

                              BusinessName  \
0            True Confections Broadway Inc   
1            True Confections Broadway Inc   
2                    Iso's Enterprises Ltd   
3                    Iso's Enterprises Ltd   
4  Tsui Hang Village Restaurant (1988) Ltd   

                      BusinessTradeName  Status  IssuedDate ExpiredDate  ...  \
0    True Confections Desert Restaurant  Issued  2006-01-10  2006-12-31  ...   
1    True Confections Desert Restaurant  Issued  2006-01-10  2006-12-31  ...   
2                Jade Rabbit Restaurant  Issued  2006-01-11  2006-12-31  ...   
3                Jade Rabbit Restaurant  Issued  2006-01-11  2006-12-31  ...   
4  Tsui Hang Village Seafood Restaurant  Issued  2005-12-08  2006-12-31  ...   

  PostalCode        LocalArea NumberofEmployees FeePaid  \
0    V6R 2B9  West Point Grey               0.0   167.0   
1    V6R 2B9  West Point Grey               0.0   558.0   
2    V6P 3E9          Marpole               0.0   330.0   
3    V6P 3E9          Marpole               0.0   558.0   
4    V6Z 1M1         Downtown               0.0   704.0   

                 ExtractDate  \
0  2019-07-21T06:48:41-07:00   
1  2019-07-21T06:48:41-07:00   
2  2019-07-21T06:48:41-07:00   
3  2019-07-21T06:48:41-07:00   
4  2019-07-21T06:48:41-07:00   

                                                Geom         Business_type_pp  \
0  {"type": "Point", "coordinates": [-123.1861020...  Hotel and Rental Agency   
1  {"type": "Point", "coordinates": [-123.1861020...              Resutaurant   
2  {"type": "Point", "coordinates": [-123.1350122...  Hotel and Rental Agency   
3  {"type": "Point", "coordinates": [-123.1350122...              Resutaurant   
4  {"type": "Point", "coordinates": [-123.1263124...  Hotel and Rental Agency   

            X          Y                     geometry  
0 -123.186102  49.264622  POINT (-123.18610 49.26462)  
1 -123.186102  49.264622  POINT (-123.18610 49.26462)  
2 -123.135012  49.204070  POINT (-123.13501 49.20407)  
3 -123.135012  49.204070  POINT (-123.13501 49.20407)  
4 -123.126312  49.277468  POINT (-123.12631 49.27747)  

[5 rows x 29 columns]

In [9]:
geom_plot = gdataset[["FOLDERYEAR", "LicenceRSN", "LocalArea", "Business_type_pp" ,"geometry"]]

In [15]:
import json
choro_json = json.loads(geom_plot[0:10000].to_json())
choro_data = alt.Data(values=choro_json['features'])

In [8]:
from shapely.geometry import Polygon

In [11]:
lat_point_list = [50.854457, 52.518172, 50.072651, 48.853033, 50.854457]
lon_point_list = [4.377184, 13.407759, 14.435935, 2.349553, 4.377184]
p = Polygon(zip(lat_point_list, lon_point_list))

In [15]:
gpd.GeoDataFrame(index=[0], crs={'init': 'epsg:4326'}, geometry=[p])

/Users/eitharelbasheer/opt/anaconda3/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))


geometry
0  POLYGON ((50.85446 4.37718, 52.51817 13.40776,...

In [23]:
alt.Chart(choro_data).mark_geoshape(
        fill='black',
        stroke='black'
    ).encode(
        alt.Color("LicenceRSN", 
                  type='quantitative', 
                  scale=alt.Scale(scheme="bluegreen"),
                  title = "Building Counts")
    )

alt.Chart(...)

In [21]:
alt.Chart(choro_data).mark_geoshape(
        stroke='red',
        strokeWidth=1
    ).encode(
    ).properties(
        width=800,
        height=800
    )

alt.Chart(...)

In [115]:
def gen_map(geodata, color_column, title, tooltip, color_scheme='bluegreen'):
    '''
    Generates Toronto neighbourhoods map with building count choropleth
    '''
    
    # Add Base Layer
    base = alt.Chart(geodata, title = title).mark_geoshape(
        stroke='black',
        strokeWidth=1
    ).encode(
    ).properties(
        width=800,
        height=800
    )
    # Add Choropleth Layer
    choro = alt.Chart(geodata).mark_geoshape(
        fill='lightgray',
        stroke='black'
    ).encode(
        alt.Color(color_column, 
                  type='quantitative', 
                  scale=alt.Scale(scheme=color_scheme),
                  title = "Building Counts"),
         tooltip=tooltip
    )
    return base + choro

In [ ]:
gen_map(choro_data, "properties.LicenceRSN", "Eithar", tooltip = ['properties.FOLDERYEAR:O','properties.Business_type_pp:O'])